In [2]:
import sys

from itertools import chain, combinations
from collections import defaultdict
from optparse import OptionParser

# from apriori import (
#     getItemSetTransactionList,
#     dataFromFile,
#     joinSet,
#     printResults,
#     returnItemsWithMinSupport,
#     runApriori,
#     subsets,
# )


itemresult = set()
freqSet = defaultdict(int)
freqSet2 = defaultdict(int)
utilSet = defaultdict(int)
utilSet2 = defaultdict(int)

freqitemset=[]
freqitemset2=[]
largeSet = dict()
minConfidence=0.5

#### from collections import defaultdict
def dataFromFile(fname):
    """Function which reads from the file and yields a generator"""
    with open(fname, "r") as file_iter:
        for line in file_iter:
            line = line.strip().rstrip(",")  # Remove trailing comma
            record = frozenset(line.split(","))
            yield record
            


def getItemSetTransactionList(data_iterator):
    transactionList = list()
    itemSet = set()
    for record in data_iterator:
        transaction = frozenset(record)
        transactionList.append(transaction)
        for item in transaction:
            itemSet.add(frozenset([item]))  # Generate 1-itemSets
    return itemSet, transactionList

def getminsup(itemSet,transactionList):
    for item in itemSet:
#         print(item)
        for transaction in transactionList:
            if item.issubset(transaction):
                freqSet[item] += 1
#                 print(freqSet)
    
    sum=0  
    for item, count in freqSet.items():
        support = float(count) / float(len(transactionList))
#         print(support)
#         print(utilSet)
        ut=utilSet[item]
        utility1=support*ut
        sum=sum+utility1
        utilSet2[item]=utility1
#         print(utilSet2)
    aveutil=sum/len(itemSet)
#     print(aveutil)
    minsup=aveutil/len(transactionList)
#     print(minsup)

    return minsup


def getfreqitem2(itemSet,transactionList,minimumSupport,freqSet,k):
    _itemSet=set()
    localSet = defaultdict(int)
    for item in itemSet:
#         print("item")
#         print(item)
        for transaction in transactionList:
            if item.issubset(transaction):
                freqSet[item] += 1
                localSet[item] += 1
#                 print(localSet)
    
    sum=0  
    for item, count in localSet.items():
        support = float(count) / float(len(transactionList))
        ut=0
        for item1,util in utilSet.items():
            if(item1.issubset(item)):
                ut=ut+float(util)
        averageutil=ut/k
#         print(averageutil)
        utility1=support*averageutil
#         print(utility1)
        utilSet2[item]=utility1
#     print("utilset",utilSet2)
#     print("localset",localSet)
    
    for item in itemSet:
#         print(item)
#         print(utilSet2[item])
        if(utilSet2[item])>=minimumSupport:
            _itemSet.add(item)
    return _itemSet


def subsets(arr):
    """ Returns non empty subsets of arr"""
    return chain(*[combinations(arr, i + 1) for i, a in enumerate(arr)])

def joinSet(itemSet, length):
    """Join a set with itself and returns the n-element itemsets"""
    itemSet=frozenset(itemSet)
    return set(
        [i.union(j) for i in itemSet for j in itemSet if len(i.union(j)) == length]
    )

def getSupport(item):
        """local function which Returns the support of an item"""
        return float(utilSet2[item])


inFile = dataFromFile("zoo.csv")
itemSet, transactionList = getItemSetTransactionList(inFile)
print("------ITEMSET--------------")
print(itemSet)
print("---------------TRANSACTION LIST----------------")
print(transactionList)



utilSet[frozenset({'1'})]=2
utilSet[frozenset({'2'})]=5
utilSet[frozenset({'3'})]=3
utilSet[frozenset({'4'})]=5
utilSet[frozenset({'5'})]=0.5
utilSet[frozenset({'6'})]=1
utilSet[frozenset({'7'})]=0.1
utilSet[frozenset({'8'})]=8
utilSet[frozenset({'9'})]=4

largeSet = dict()
    # Global dictionary which stores (key=n-itemSets,value=support)
    # which satisfy minSupport

assocRules = dict()
    # Dictionary which stores Association Rules
minsup=getminsup(itemSet,transactionList)
print("MINIMUM SUPPORT",minsup)
oneCSet = getfreqitem2(itemSet, transactionList, minsup,freqSet,1)
# print(oneCSet)

currentLSet = oneCSet
k = 2
# currentLSet = joinSet(currentLSet, k)
# print("2 itemset")
# print(currentLSet)
# freqitemset2 = getfreqitem2(currentLSet, transactionList, minsup,freqSet,k)
# print("freq item 2")
# print(freqitemset2)
# k=3
# currentLSet = joinSet(oneCSet, k)
# print(currentLSet)
# oneCSet = getfreqitem2(currentLSet, transactionList, minsup,freqSet,k)
# print("freq item 3")
# print(oneCSet)

while currentLSet != set([]):
    largeSet[k - 1] = currentLSet
    currentLSet = joinSet(currentLSet, k)
#     print(currentLSet)
    currentCSet = getfreqitem2(
        currentLSet, transactionList, minsup,freqSet,k
    )
    currentLSet = currentCSet
#     print(currentLSet)
    k = k + 1

    
# print(largeSet)
       
toRetItems = []
for key, value in largeSet.items():
    toRetItems.extend([(tuple(item), getSupport(item)) for item in value])

toRetRules = []
for key, value in list(largeSet.items())[1:]:
    for item in value:
        _subsets = map(frozenset, [x for x in subsets(item)])
        for element in _subsets:
            remain = item.difference(element)
            if len(remain) > 0:
                confidence = getSupport(item) / getSupport(element)
                if confidence >= minConfidence:
                    lift=confidence/getSupport(remain)
                    toRetRules.append(((tuple(element), tuple(remain)), confidence,lift))

print("\n------------------------ FREQUENT ITEMSET:")
"""prints the generated itemsets sorted by support and the confidence rules sorted by confidence"""
for item, support in sorted(toRetItems, key=lambda x: x[1]):
    print("item: %s , %.3f" % (str(item), support))
    
from operator import itemgetter
res = sorted(toRetRules, key = itemgetter(2),reverse=True)
# print(str(res))
print("\n------------------------ RULES:")
for rule, confidence,lift in (res):
    pre, post = rule
    print("Rule: %s ==> %s , %.3f, %.3f" % (str(pre), str(post), confidence, lift))

print(len(res))
# for rule, confidence in sorted(toRetRules, key=lambda x: x[1]):
#     pre, post = rule
#     print("Rule: %s ==> %s , %.3f" % (str(pre), str(post), confidence))



------ITEMSET--------------
{frozenset({'6'}), frozenset({'5'}), frozenset({'2'}), frozenset({'4'}), frozenset({'3'}), frozenset({'7'}), frozenset({'1'}), frozenset({'0'}), frozenset({'8'})}
---------------TRANSACTION LIST----------------
[frozenset({'1', '4', '0'}), frozenset({'1', '4', '0'}), frozenset({'0', '4', '1'}), frozenset({'1', '4', '0'}), frozenset({'1', '4', '0'}), frozenset({'1', '4', '0'}), frozenset({'1', '4', '0'}), frozenset({'0', '4', '1'}), frozenset({'0', '4', '1'}), frozenset({'1', '4', '0'}), frozenset({'1', '4', '0'}), frozenset({'0', '2', '1'}), frozenset({'0', '4', '1'}), frozenset({'0', '7', '1'}), frozenset({'0', '4', '7', '1'}), frozenset({'6', '0', '7', '1'}), frozenset({'0', '2', '1'}), frozenset({'1', '4', '0'}), frozenset({'0', '4', '1'}), frozenset({'0', '1'}), frozenset({'0', '2', '1'}), frozenset({'0', '2', '1'}), frozenset({'1', '4', '0'}), frozenset({'0', '2', '1'}), frozenset({'6', '0', '1'}), frozenset({'0', '4', '1', '5'}), frozenset({'0', '4', '